In [1]:
!pip install -e ..[dev,training]

Obtaining file:///ldap_home/qishuai.zhong/Projects/punctuator
  Preparing metadata (setup.py) ... done


  Attempting uninstall: distilbert-punctuator
    Found existing installation: distilbert-punctuator 0.2.1
    Uninstalling distilbert-punctuator-0.2.1:
      Successfully uninstalled distilbert-punctuator-0.2.1
  Running setup.py develop for distilbert-punctuator


In [2]:
from datasets import load_dataset

dataset = load_dataset("conll2003")

/ldap_home/qishuai.zhong/miniconda3/envs/punctuator_env/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Reusing dataset conll2003 (/ldap_home/qishuai.zhong/.cache/huggingface/datasets/conll2003/conll2003/1.0.0/9a4d16a94f8674ba3466315300359b0acd891b68b6c8743ddf60b9c702adce98)
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 629.68it/s]


In [3]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'tokens', 'pos_tags', 'chunk_tags', 'ner_tags'],
        num_rows: 14041
    })
    validation: Dataset({
        features: ['id', 'tokens', 'pos_tags', 'chunk_tags', 'ner_tags'],
        num_rows: 3250
    })
    test: Dataset({
        features: ['id', 'tokens', 'pos_tags', 'chunk_tags', 'ner_tags'],
        num_rows: 3453
    })
})

In [4]:
train_dataset = dataset["train"]
validation_dataset = dataset["validation"]

print(train_dataset, validation_dataset)

Dataset({
    features: ['id', 'tokens', 'pos_tags', 'chunk_tags', 'ner_tags'],
    num_rows: 14041
}) Dataset({
    features: ['id', 'tokens', 'pos_tags', 'chunk_tags', 'ner_tags'],
    num_rows: 3250
})


In [5]:
# sample 5000 for training

import random

index_list = [index for index, _ in enumerate(train_dataset["tokens"])]
random.seed(7)

sample_indexes = random.sample(index_list, 5000)
print(sample_indexes[:10])

training_corpus = [sequence for index, sequence in enumerate(train_dataset["tokens"]) if index in sample_indexes]
training_tags = [tags for index, tags in enumerate(train_dataset["ner_tags"]) if index in sample_indexes]

print(training_corpus[:5], [len(sequence) for sequence in training_corpus[:5]],  training_tags[:5], [len(sequence) for sequence in training_tags[:5]])


[5305, 2471, 6468, 10664, 791, 1186, 13455, 8779, 1542, 5991]
[['BRUSSELS', '1996-08-22'], ['The', 'European', 'Commission', 'said', 'on', 'Thursday', 'it', 'disagreed', 'with', 'German', 'advice', 'to', 'consumers', 'to', 'shun', 'British', 'lamb', 'until', 'scientists', 'determine', 'whether', 'mad', 'cow', 'disease', 'can', 'be', 'transmitted', 'to', 'sheep', '.'], ['"', 'We', 'do', "n't", 'support', 'any', 'such', 'recommendation', 'because', 'we', 'do', "n't", 'see', 'any', 'grounds', 'for', 'it', ',', '"', 'the', 'Commission', "'s", 'chief', 'spokesman', 'Nikolaus', 'van', 'der', 'Pas', 'told', 'a', 'news', 'briefing', '.'], ['He', 'said', 'further', 'scientific', 'study', 'was', 'required', 'and', 'if', 'it', 'was', 'found', 'that', 'action', 'was', 'needed', 'it', 'should', 'be', 'taken', 'by', 'the', 'European', 'Union', '.'], ['The', 'EU', "'s", 'scientific', 'veterinary', 'and', 'multidisciplinary', 'committees', 'are', 'due', 'to', 're-examine', 'the', 'issue', 'early', 'ne

In [6]:
# get the longest sentence
 
lengths = [len(text) for text in training_corpus]
print(max(lengths))

113


In [12]:
from dbpunctuator.training import NERTrainingArguments, NERTrainingPipeline
from datasets import load_dataset

training_args = NERTrainingArguments(
    training_corpus = training_corpus,
    validation_corpus = validation_dataset["tokens"],
    training_tags = training_tags,
    validation_tags = validation_dataset["ner_tags"],
    model_name_or_path="distilbert-base-cased",
    tokenizer_name="distilbert-base-cased",
    epoch=20,
    batch_size=32,
    model_storage_dir="../models/corll_ner_no_rdrop_sampled",
    addtional_model_config={"dropout": 0.3, "attention_dropout": 0.3},
    gpu_device=1,
    warm_up_steps=500,
    r_drop=False,
    tensorboard_log_dir="../runs/corll_ner_no_rdrop_sampled",
    label2id={
        "O": 0,
        "B-PER": 1,
        "I-PER": 2,
        "B-ORG": 3,
        "I-ORG": 4,
        "B-LOC": 5,
        "I-LOC": 6,
        "B-MISC": 7,
        "I-MISC": 8,
    }
)

training_pipeline = NERTrainingPipeline(training_args)
training_pipeline.run()

2022-09-10 23:13:16,440 - INFO - general_ner_train.py:111 - general_ner_train.tokenize - 44779 - tokenize data
2022-09-10 23:13:27,218 - INFO - general_ner_train.py:143 - general_ner_train.tokenize - 44779 - unique tag ids: {0, 1, 2, 3, 4, 5, 6, 7, 8}, id2label: {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8: 'I-MISC'}
2022-09-10 23:13:27,230 - INFO - general_ner_train.py:154 - general_ner_train.tokenize - 44779 - class weights: [1, 1.19, 1.54, 1.34, 1.91, 1.16, 3.06, 1.83, 2.85], id2label: {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8: 'I-MISC'}
2022-09-10 23:13:27,231 - INFO - general_ner_train.py:275 - general_ner_train._encode_tags - 44779 - encoding tags
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5000/5000 [00:00<00:00, 9391.99it/s]
2022-09-10 23:13:27,766 - INFO - general_ner_train.py:275 - general_ne

Processing batch: 59:  38%|█████████████████████████▏                                         | 59/157 [00:09<00:15,  6.23it/s, Last_loss=1.99, Avg_cum_loss=2.12]


Processing batch: 92:  58%|██████████████████████████████████████▊                            | 91/157 [00:14<00:10,  6.34it/s, Last_loss=1.65, Avg_cum_loss=2.01]


Processing batch: 124:  79%|███████████████████████████████████████████████████▎             | 124/157 [00:19<00:05,  6.36it/s, Last_loss=1.14, Avg_cum_loss=1.85]


Processing batch: 157: 100%|█████████████████████████████████████████████████████████████████| 157/157 [00:24<00:00,  6.31it/s, Last_loss=0.86, Avg_cum_loss=1.63]



...

Processing batch: 133:  84%|██████████████████████████████████████████████████████▋          | 132/157 [00:20<00:03,  6.36it/s, Last_loss=0.02, Avg_cum_loss=0.02]


Processing batch: 157: 100%|█████████████████████████████████████████████████████████████████| 157/157 [00:24<00:00,  6.38it/s, Last_loss=0.14, Avg_cum_loss=0.03]

Processing batch: 11:  10%|██████▌                                                            | 10/102 [00:00<00:04, 20.34it/s, Last_loss=0.09, Avg_cum_loss=0.07]


Processing batch: 53:  51%|██████████████████████████████████▏                                | 52/102 [00:02<00:02, 20.15it/s, Last_loss=0.02, Avg_cum_loss=0.06]


Processing batch: 93:  90%|████████████████████████████████████████████████████████████▍      | 92/102 [00:04<00:00, 19.52it/s, Last_loss=0.09, Avg_cum_loss=0.07]


Processing batch: 102: 100%|█████████████████████████████████████████████████████████████████| 102/102 [00:05<00:00, 20.04it/s, Last_loss=0.01, Avg_cum_loss=0.07]
2022-09-10 23:23:25,549 - INFO - general_ner_train.py:236 - general_ner_train.fine_tune - 44779 - Epoch: 20 | Epoch Time: 0m 29s
2022-09-10 23:23:25,550 - INFO - general_ner_train.py:239 - general_ner_train.fine_tune - 44779 - 	Train Loss: 0.025 | Train Acc: 99.28%
2022-09-10 23:23:25,550 - INFO - general_ner_train.py:242 - general_ner_train.fine_tune - 44779 - 	 Val. Loss: 0.066 |  Val. Acc: 98.40%
Processing epoch: 20: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [09:55<00:00, 29.79s/it]
2022-09-10 23:23:25,554 - INFO - general_ner_train.py:267 - general_ner_train.persist - 44779 - persist fine-tuned model
2022-09-10 23:23:26,055 - INFO - general_ner_train.py:272 - general_ner_train.persist - 44779 - fine-tuned model stored to ../models/corll_ner_no_rdro

In [14]:
from dbpunctuator.training import NERTrainingArguments, NERTrainingPipeline
from datasets import load_dataset

training_args = NERTrainingArguments(
    training_corpus = train_dataset["tokens"],
    validation_corpus = validation_dataset["tokens"],
    training_tags = train_dataset["ner_tags"],
    validation_tags = validation_dataset["ner_tags"],
    model_name_or_path="distilbert-base-cased",
    tokenizer_name="distilbert-base-cased",
    epoch=20,
    batch_size=32,
    model_storage_dir="../models/corll_ner_rdrop",
    addtional_model_config={"dropout": 0.3, "attention_dropout": 0.3},
    gpu_device=1,
    warm_up_steps=500,
    r_drop=True,
    tensorboard_log_dir="../runs/corll_ner_rdrop",
    label2id={
        "O": 0,
        "B-PER": 1,
        "I-PER": 2,
        "B-ORG": 3,
        "I-ORG": 4,
        "B-LOC": 5,
        "I-LOC": 6,
        "B-MISC": 7,
        "I-MISC": 8,
    }
)

training_pipeline = NERTrainingPipeline(training_args)
training_pipeline.run()

2022-09-10 23:46:34,773 - INFO - general_ner_train.py:111 - general_ner_train.tokenize - 44779 - tokenize data
2022-09-10 23:46:45,050 - INFO - general_ner_train.py:143 - general_ner_train.tokenize - 44779 - unique tag ids: {0, 1, 2, 3, 4, 5, 6, 7, 8}, id2label: {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8: 'I-MISC'}
2022-09-10 23:46:45,075 - INFO - general_ner_train.py:154 - general_ner_train.tokenize - 44779 - class weights: [1, 1.21, 1.58, 1.31, 1.85, 1.15, 3.0, 1.87, 2.94], id2label: {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8: 'I-MISC'}
2022-09-10 23:46:45,076 - INFO - general_ner_train.py:275 - general_ner_train._encode_tags - 44779 - encoding tags
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 14041/14041 [00:01<00:00, 9935.48it/s]
2022-09-10 23:46:46,492 - INFO - general_ner_train.py:275 - general_ner

Processing batch: 59:  13%|█████████                                                          | 59/439 [00:17<01:55,  3.29it/s, Last_loss=2.15, Avg_cum_loss=2.28]


Processing batch: 92:  21%|█████████████▉                                                     | 91/439 [00:27<01:45,  3.29it/s, Last_loss=1.78, Avg_cum_loss=2.18]


Processing batch: 124:  28%|██████████████████▎                                              | 124/439 [00:37<01:35,  3.29it/s, Last_loss=1.35, Avg_cum_loss=2.02]


Processing batch: 157:  36%|███████████████████████▏                                         | 157/439 [00:47<01:25,  3.28it/s, Last_loss=0.97, Avg_cum_loss=1.83]


...

Processing batch: 418:  95%|█████████████████████████████████████████████████████████████▋   | 417/439 [02:06<00:06,  3.30it/s, Last_loss=0.06, Avg_cum_loss=0.03]


Processing batch: 439: 100%|█████████████████████████████████████████████████████████████████| 439/439 [02:13<00:00,  3.29it/s, Last_loss=0.04, Avg_cum_loss=0.03]

Processing batch: 13:  13%|████████▌                                                          | 13/102 [00:01<00:08, 10.53it/s, Last_loss=0.08, Avg_cum_loss=0.07]


Processing batch: 52:  51%|██████████████████████████████████▏                                | 52/102 [00:04<00:04, 10.55it/s, Last_loss=0.11, Avg_cum_loss=0.06]


Processing batch: 92:  89%|███████████████████████████████████████████████████████████▊       | 91/102 [00:08<00:01, 10.47it/s, Last_loss=0.12, Avg_cum_loss=0.07]


Processing batch: 102: 100%|█████████████████████████████████████████████████████████████████| 102/102 [00:09<00:00, 10.57it/s, Last_loss=0.00, Avg_cum_loss=0.07]
2022-09-11 00:13:01,439 - INFO - general_ner_train.py:236 - general_ner_train.fine_tune - 44779 - Epoch: 11 | Epoch Time: 2m 23s
2022-09-11 00:13:01,440 - INFO - general_ner_train.py:239 - general_ner_train.fine_tune - 44779 - 	Train Loss: 0.030 | Train Acc: 99.54%
2022-09-11 00:13:01,441 - INFO - general_ner_train.py:242 - general_ner_train.fine_tune - 44779 - 	 Val. Loss: 0.072 |  Val. Acc: 98.86%
Processing epoch: 11:  55%|████████████████████████████████████████████████████████                                              | 11/20 [26:12<21:26, 142.97s/it]
2022-09-11 00:13:01,443 - INFO - general_ner_train.py:267 - general_ner_train.persist - 44779 - persist fine-tuned model
2022-09-11 00:13:01,965 - INFO - general_ner_train.py:272 - general_ner_train.persist - 44779 - fine-tuned model stored to ../models/corll_ner_rdrop


In [9]:
test_dataset = dataset["test"]

In [13]:
from dbpunctuator.training import EvaluationArguments, EvaluationPipeline

validation_args = EvaluationArguments(
    evaluation_corpus=test_dataset["tokens"],
    evaluation_tags=test_dataset["ner_tags"],
    model_name_or_path="../models/corll_ner_no_rdrop_sampled",
    tokenizer_name="distilbert-base-cased",
    batch_size=32,
    gpu_device=1,
)

validate_pipeline = EvaluationPipeline(validation_args)
validate_pipeline.run()

2022-09-10 23:43:02,499 - INFO - evalute.py:66 - evalute.tokenize - 44779 - tokenize data
2022-09-10 23:43:10,577 - INFO - evalute.py:138 - evalute._encode_tags - 44779 - encoding tags
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3453/3453 [00:00<00:00, 9346.95it/s]
2022-09-10 23:43:10,955 - INFO - evalute.py:82 - evalute.validate - 44779 - start validation
Processing batch: 108: 100%|██████████████████████████████████████████████████████████████████████████████| 108/108 [00:05<00:00, 21.34it/s, Last_batch_loss=0.13]
2022-09-10 23:43:16,071 - INFO - evalute.py:132 - evalute.validate - 44779 - validation report: 
               precision    recall  f1-score   support

       B-LOC     0.8831    0.9329    0.9073      1668
      B-MISC     0.7849    0.8162    0.8003       702
       B-ORG     0.8830    0.8724    0.8776      1661
       B-PER     0.9540    0.9487    0.9513      1617
       I-LOC     0.7389    

In [11]:
from dbpunctuator.training import EvaluationArguments, EvaluationPipeline

validation_args = EvaluationArguments(
    evaluation_corpus=test_dataset["tokens"],
    evaluation_tags=test_dataset["ner_tags"],
    model_name_or_path="../models/corll_ner_rdrop_sampled",
    tokenizer_name="distilbert-base-cased",
    batch_size=32,
    gpu_device=1,
)

validate_pipeline = EvaluationPipeline(validation_args)
validate_pipeline.run()

2022-09-10 23:12:35,885 - INFO - evalute.py:66 - evalute.tokenize - 44779 - tokenize data
2022-09-10 23:12:44,473 - INFO - evalute.py:138 - evalute._encode_tags - 44779 - encoding tags
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3453/3453 [00:00<00:00, 9495.29it/s]
2022-09-10 23:12:44,845 - INFO - evalute.py:82 - evalute.validate - 44779 - start validation
Processing batch: 108: 100%|██████████████████████████████████████████████████████████████████████████████| 108/108 [00:04<00:00, 21.64it/s, Last_batch_loss=0.24]
2022-09-10 23:12:49,895 - INFO - evalute.py:132 - evalute.validate - 44779 - validation report: 
               precision    recall  f1-score   support

       B-LOC     0.9278    0.9017    0.9146      1668
      B-MISC     0.7334    0.8348    0.7808       702
       B-ORG     0.8659    0.8826    0.8742      1661
       B-PER     0.9529    0.9511    0.9520      1617
       I-LOC     0.7835    

In [15]:
from dbpunctuator.training import EvaluationArguments, EvaluationPipeline

validation_args = EvaluationArguments(
    evaluation_corpus=test_dataset["tokens"],
    evaluation_tags=test_dataset["ner_tags"],
    model_name_or_path="../models/corll_ner_no_rdrop",
    tokenizer_name="distilbert-base-cased",
    batch_size=32,
    gpu_device=1,
)

validate_pipeline = EvaluationPipeline(validation_args)
validate_pipeline.run()

2022-09-11 00:13:46,102 - INFO - evalute.py:66 - evalute.tokenize - 44779 - tokenize data
2022-09-11 00:13:54,662 - INFO - evalute.py:138 - evalute._encode_tags - 44779 - encoding tags
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3453/3453 [00:00<00:00, 11301.89it/s]
2022-09-11 00:13:54,976 - INFO - evalute.py:82 - evalute.validate - 44779 - start validation
Processing batch: 108: 100%|██████████████████████████████████████████████████████████████████████████████| 108/108 [00:05<00:00, 21.51it/s, Last_batch_loss=0.04]
2022-09-11 00:14:00,058 - INFO - evalute.py:132 - evalute.validate - 44779 - validation report: 
               precision    recall  f1-score   support

       B-LOC     0.9243    0.9371    0.9306      1668
      B-MISC     0.8039    0.8234    0.8135       702
       B-ORG     0.8792    0.9031    0.8910      1661
       B-PER     0.9648    0.9505    0.9576      1617
       I-LOC     0.8417    

In [16]:
from dbpunctuator.training import EvaluationArguments, EvaluationPipeline

validation_args = EvaluationArguments(
    evaluation_corpus=test_dataset["tokens"],
    evaluation_tags=test_dataset["ner_tags"],
    model_name_or_path="../models/corll_ner_rdrop",
    tokenizer_name="distilbert-base-cased",
    batch_size=32,
    gpu_device=1,
)

validate_pipeline = EvaluationPipeline(validation_args)
validate_pipeline.run()

2022-09-11 00:14:13,330 - INFO - evalute.py:66 - evalute.tokenize - 44779 - tokenize data
2022-09-11 00:14:20,863 - INFO - evalute.py:138 - evalute._encode_tags - 44779 - encoding tags
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3453/3453 [00:00<00:00, 12193.31it/s]
2022-09-11 00:14:21,154 - INFO - evalute.py:82 - evalute.validate - 44779 - start validation
Processing batch: 108: 100%|██████████████████████████████████████████████████████████████████████████████| 108/108 [00:05<00:00, 21.28it/s, Last_batch_loss=0.21]
2022-09-11 00:14:26,287 - INFO - evalute.py:132 - evalute.validate - 44779 - validation report: 
               precision    recall  f1-score   support

       B-LOC     0.9273    0.9323    0.9297      1668
      B-MISC     0.7931    0.8462    0.8187       702
       B-ORG     0.9106    0.8832    0.8967      1661
       B-PER     0.9404    0.9666    0.9533      1617
       I-LOC     0.7940    

## Punctuator

In [ ]:
from dbpunctuator.training import generate_training_assets
from dbpunctuator.training import NERTrainingArguments, NERTrainingPipeline

data_file_path="../training_data/english_token_tag_data.txt"

training_corpus, training_tags, validation_corpus, validation_tags, label2id, id2label = generate_training_assets(data_file_path, 100, 300, 0.25)

training_args = NERTrainingArguments(
    training_corpus = training_corpus,
    validation_corpus = validation_corpus,
    training_tags = training_tags,
    validation_tags = validation_tags,
    model_name_or_path="distilbert-base-cased",
    tokenizer_name="distilbert-base-cased",
    epoch=20,
    batch_size=32,
    model_storage_dir="../models/english_punctuator_rdrop",
    addtional_model_config={"dropout": 0.3, "attention_dropout": 0.3},
    gpu_device=1,
    warm_up_steps=500,
    r_drop=True,
    tensorboard_log_dir="../runs/english_punctuator_rdrop",
    label2id=label2id
)

training_pipeline = NERTrainingPipeline(training_args)
training_pipeline.run()

2022-09-11 13:45:27,511 - INFO - punctuation_data_process.py:117 - punctuation_data_process.generate_training_assets - 61820 - load training data
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████| 8241655/8241655 [00:06<00:00, 1214604.30it/s]
2022-09-11 13:45:39,013 - INFO - punctuation_data_process.py:126 - punctuation_data_process.generate_training_assets - 61820 - data sample: ['quarterly', 'profits', 'at', 'us', 'media', 'giant', 'timewarner', 'jumped', '<NUM>', 'to', '<CURRENCY>', 'for', 'the', 'three', 'months', 'to', 'december', 'from', '<CURRENCY>', 'yearearlier', 'the', 'firm', 'which', 'is', 'now', 'one', 'of', 'the', 'biggest', 'investors', 'in', 'google', 'benefited', 'from', 'sales', 'of', 'highspeed', 'internet', 'connections', 'and', 'higher', 'advert', 'sales', 'timewarner', 'said', 'fourth', 'quarter', 'sales', 'rose', '<NUM>', 'to', '<CURRENCY>', 'from', '<CURRENCY>', 'its', 'profits', 'were', 'buoyed',